In [ ]:
# Step 1: Install and Import Dependencies
!pip install torch torchvision matplotlib --quiet

import torch
import torch.nn as nn
import torch.optim as optim
from torchvision import datasets, transforms
from torch.utils.data import Dataset, DataLoader
import matplotlib.pyplot as plt
import numpy as np
import random


In [ ]:
# Step 2: Create Siamese Dataset
class SiameseMNIST(Dataset):
    def __init__(self, train=True):
        self.mnist = datasets.MNIST(
            root="./data", train=train, download=True,
            transform=transforms.ToTensor()
        )

        # Group images by label
        self.data_by_class = {i: [] for i in range(10)}
        for img, label in self.mnist:
            self.data_by_class[label].append(img)

        self.classes = list(self.data_by_class.keys())

    def __getitem__(self, idx):
        label = random.choice(self.classes)

        # Positive pair
        img1 = random.choice(self.data_by_class[label])
        img2 = random.choice(self.data_by_class[label])
        similarity = 1

        # Negative pair
        if random.random() < 0.5:
            neg_label = random.choice([c for c in self.classes if c != label])
            img2 = random.choice(self.data_by_class[neg_label])
            similarity = 0

        return img1, img2, torch.tensor([similarity], dtype=torch.float32)

    def __len__(self):
        return 60000


In [ ]:
# Step 3: Build the Siamese Neural Network
class SiameseNetwork(nn.Module):
    def __init__(self):
        super().__init__()
        self.conv = nn.Sequential(
            nn.Conv2d(1, 32, 5),
            nn.ReLU(),
            nn.MaxPool2d(2),

            nn.Conv2d(32, 64, 5),
            nn.ReLU(),
            nn.MaxPool2d(2)
        )

        self.fc = nn.Sequential(
            nn.Linear(64 * 4 * 4, 256),
            nn.ReLU(),
            nn.Linear(256, 64)  # Embedding size
        )

    def forward_once(self, x):
        x = self.conv(x)
        x = x.view(x.size()[0], -1)
        return self.fc(x)

    def forward(self, x1, x2):
        return self.forward_once(x1), self.forward_once(x2)


In [ ]:
# Step 4: Define Contrastive Loss
class ContrastiveLoss(nn.Module):
    def __init__(self, margin=2.0):
        super().__init__()
        self.margin = margin

    def forward(self, emb1, emb2, label):
        distances = torch.nn.functional.pairwise_distance(emb1, emb2)
        loss = torch.mean(
            label * distances**2 +
            (1 - label) * torch.clamp(self.margin - distances, min=0)**2
        )
        return loss


In [ ]:
# Step 5: Training Loop
device = "cuda" if torch.cuda.is_available() else "cpu"

train_data = SiameseMNIST(train=True)
train_loader = DataLoader(train_data, batch_size=128, shuffle=True)

model = SiameseNetwork().to(device)
criterion = ContrastiveLoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

epochs = 5

for epoch in range(epochs):
    total_loss = 0
    for img1, img2, label in train_loader:
        img1, img2, label = img1.to(device), img2.to(device), label.to(device)

        emb1, emb2 = model(img1, img2)
        loss = criterion(emb1, emb2, label)

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        total_loss += loss.item()

    print(f"Epoch {epoch+1}/{epochs}, Loss: {total_loss/len(train_loader):.4f}")


In [ ]:
# Step 6: Testing & Visualization
test_data = SiameseMNIST(train=False)

img1, img2, lbl = test_data[500]

model.eval()
with torch.no_grad():
    e1, e2 = model(img1.unsqueeze(0).to(device),
                   img2.unsqueeze(0).to(device))
    dist = torch.nn.functional.pairwise_distance(e1, e2).item()

plt.subplot(1,2,1)
plt.imshow(img1.squeeze(), cmap='gray')
plt.title("Image 1")

plt.subplot(1,2,2)
plt.imshow(img2.squeeze(), cmap='gray')
plt.title("Image 2")

plt.show()

print("True Similarity Label (1=Similar, 0=Dissimilar):", int(lbl.item()))
print("Embedding Distance:", dist)
